In [ ]:
import pandas as pd
import numpy as np

from bs4 import BeautifulSoup
import requests

import datetime

import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)


import json
import geopandas as gpd
import pygeos

import altair as alt

In [ ]:
#Get well completion reports data
wellcompletion_plss_df = pd.read_csv(r"assets/clean_data/well_completion_clean.csv")
wellcompletion_plss_df = wellcompletion_plss_df[~wellcompletion_plss_df.YEARWORKENDED.isna()].copy()
wellcompletion_plss_df.YEARWORKENDED = wellcompletion_plss_df.YEARWORKENDED.astype('int64')
wellcompletion_plss_df.rename(columns={'YEARWORKENDED':'year'}, inplace=True)

#Precipitation data
all_years_precipitation_station = pd.read_csv(r"assets/clean_data/precipitation_stations.csv")
# Set the county name to be camel case for join
all_years_precipitation_station.COUNTY = all_years_precipitation_station.COUNTY.str.title()


#Reservoir data
weekly_reservoir_station_data = pd.read_csv(r"assets/clean_data/weekly_reservoir_station_data.csv")

#Drought years determined visually as per chart in notebook drought_reservoir_data
drought_years = [2019, 2020, 2021, 2018, 2012, 2013, 2014,2015, 2016, 2007, 2008, 2009 ]
wellcompletion_plss_df['drought_year'] = np.where(wellcompletion_plss_df.year.isin(drought_years), 1, 0)

C:\Users\SimiTalkar\AppData\Local\Temp\ipykernel_15832\2515158002.py:2: DtypeWarning: Columns (4) have mixed types. Specify dtype option on import or set low_memory=False.
  wellcompletion_plss_df = pd.read_csv(r"assets/clean_data/well_completion_clean.csv")


In [ ]:
all_years_precipitation_station.columns = [col.strip() for col in all_years_precipitation_station.columns]
all_years_precipitation_station.columns

Index(['station_id', 'STATION NAME', 'OCT', 'NOV', 'DEC', 'JAN', 'FEB', 'MAR',
       'APR', 'MAY', 'JUN', 'JUL', 'AUG', 'SEP', 'average_year_precip', 'year',
       'LATITUDE', 'LONGITUDE', 'COUNTY'],
      dtype='object')

In [ ]:
# load the plss shapefile (these only include TRS areas that are within the San Joaquin subbasin)
SJ_subbasin_plss = gpd.read_file("assets/clean_data/plss_subbasin.geojson")
# aggregate by TownshipRange
SJ_subbasin_plss_range = SJ_subbasin_plss.dissolve(by='TownshipRange').reset_index()
SJ_subbasin_plss_range.explore()

In [ ]:
# load the plss shapefile (these only include TRS areas that are within the San Joaquin subbasin)
california_plss = gpd.read_file("assets/clean_data/california_plss.geojson")
# aggregate by TownshipRange
california_plss_range = california_plss.dissolve(by='TownshipRange').reset_index()
#california_plss_range.explore()

In [ ]:
# create wells geodataframe
# In case of geographic coordinates, it is assumed that longitude is captured by x coordinates and latitude by y.
 
precipitation_data_gdf = gpd.GeoDataFrame(all_years_precipitation_station, geometry=gpd.points_from_xy(all_years_precipitation_station.LONGITUDE, all_years_precipitation_station.LATITUDE))
#Set the coordinate reference system (the projection that denote the axis for the points)
precipitation_data_gdf = precipitation_data_gdf.set_crs('epsg:4326')
# spatial join based on geometry
precipitation_data_plss = precipitation_data_gdf.sjoin(SJ_subbasin_plss, how="left")
precipitation_california_data_plss = precipitation_data_gdf.sjoin(california_plss, how="left")
precipitation_data_plss = precipitation_data_plss[~precipitation_data_plss.MTRS.isna()].copy()
precipitation_california_data_plss = precipitation_california_data_plss[~precipitation_california_data_plss.MTRS.isna()].copy()

# drop the ones that aren't in the san joaquin valley basin


In [ ]:
precipitation_data_plss.shape #((144, 29)

(160, 29)

In [ ]:
precipitation_data_plss.explore()

In [ ]:
print(precipitation_california_data_plss.shape) #(1538, 29)
precipitation_california_data_plss.explore()

(1708, 29)


In [ ]:
len(set(wellcompletion_plss_df.TownshipRange).intersection(set(precipitation_data_plss.TownshipRange)))

16

In [ ]:
well_precip_tr = list(set(wellcompletion_plss_df.TownshipRange).intersection(set(precipitation_data_plss.TownshipRange)))

### The precipitation  stations are disperesed along the length of the San Joaquin river basin (almost uniformly)
- A decision is to be made about the precipitation in the TownshipRanges where there is no station to provide data 
- We can average out the entire regions precipitation

In [ ]:
combined_well_precip_reser_df = wellcompletion_plss_df.merge(precipitation_data_plss, how='left', on=['TownshipRange', 'COUNTY', 'year'], indicator=True, suffixes = ('_wellcompletion', '_precipitation_station'))
#create a column with average precipitation across all toenship ranges for each year
#For toenship ranges with no precipitation data (since station is not present in that township, we use this average yearly amount )

combined_well_precip_reser_df['avg_precip_all_tr_year'] = combined_well_precip_reser_df.groupby('year')['average_year_precip'].transform('mean')

## THere are several year for which we do not have precipitation data, remove them
combined_well_precip_reser_df = combined_well_precip_reser_df[~combined_well_precip_reser_df['avg_precip_all_tr_year'].isnull()].copy()

combined_well_precip_reser_df['average_year_precip_corrected'] = np.where(combined_well_precip_reser_df['average_year_precip'].isnull(), combined_well_precip_reser_df['avg_precip_all_tr_year'], combined_well_precip_reser_df['average_year_precip'] )

In [ ]:
print(combined_well_precip_reser_df.shape, wellcompletion_plss_df.shape, precipitation_data_plss.shape)


(98080, 62) (98080, 34) (160, 29)


In [ ]:
pd.options.display.max_columns=100
combined_well_precip_reser_df.sample(5)

LATITUDE_wellcompletion  LONGITUDE_wellcompletion TOWNSHIP RANGE  \
9499                 36.771700               -120.087300      13S   17E   
92348                36.392470               -119.287650      18S   25E   
4504                 36.598200               -119.745930      15S   20E   
32268                35.069510               -118.984690      11N   20W   
65030                38.217556               -121.246225      04N   07E   

      SECTION                     WELLLOCATION         CITY       COUNTY  \
9499     26.0                    2040 N LASSEN       KERMAN       Fresno   
92348       5           NO AVE 328 & WS RD 132      VISALIA       Tulare   
4504     25.0                   9117 S. ROWELL       FRESNO       Fresno   
32268       2  MARICOPA HWY & S SABODAN STREET  BAKERSFIELD         Kern   
65030     7.0                5882 E Collier RD      Acampo   San Joaquin   

       BOTTOMOFPERFORATEDINTERVAL  TOPOFPERFORATEDINTERVAL  \
9499                        400.0                    240.0   
92348                       260.0                    160.0   
4504                        300.0                    240.0   
32268                       920.0                    900.0   
65030                       300.0                    260.0   

       GROUNDSURFACEELEVATION  STATICWATERLEVEL  \
9499                      NaN              96.0   
92348                     NaN             138.0   
4504                      NaN             104.0   
32268                     NaN             445.0   
65030                     NaN               NaN   

                                           RECORDTYPE          USE  \
9499   WellCompletion/New/Production or Monitoring/NA     Domestic   
92348  WellCompletion/New/Production or Monitoring/NA  Agriculture   
4504   WellCompletion/New/Production or Monitoring/NA     Domestic   
32268  WellCompletion/New/Production or Monitoring/NA  Agriculture   
65030  WellCompletion/New/Production or Monitoring/NA     Domestic   

            WCRNUMBER  TOTALDRILLDEPTH  TOTALCOMPLETEDDEPTH DATEWORKENDED  \
9499   WCR2014-012709              NaN                420.0    2014-07-10   
92348  WCR2016-012441              NaN                270.0    2016-08-01   
4504   WCR2016-016187              NaN                310.0    2016-01-14   
32268  WCR2016-015242              NaN               1820.0    2016-03-20   
65030  WCR2020-014052            300.0                300.0    2020-08-27   

       CASINGDIAMETER  TOTALCOMPLETEDDEPTH_CORRECTED DATEWORKENDED_CORRECTED  \
9499            5.000                          420.0              2014-07-10   
92348          10.750                          270.0              2016-08-01   
4504            6.625                          310.0              2016-01-14   
32268          30.000                         1820.0              2016-03-20   
65030             NaN                          300.0              2020-08-27   

       year  MONTHWORKENDED        geometry_wellcompletion  \
9499   2014             7.0      POINT (-120.0873 36.7717)   
92348  2016             8.0    POINT (-119.28765 36.39247)   
4504   2016             1.0     POINT (-119.74593 36.5982)   
32268  2016             3.0    POINT (-118.98469 35.06951)   
65030  2020             8.0  POINT (-121.246225 38.217556)   

       index_right_wellcompletion  OBJECTID_wellcompletion  \
9499                       6147.0                  45046.0   
92348                      8630.0                  59727.0   
4504                       7181.0                  50773.0   
32268                     14256.0                 149558.0   
65030                       103.0                   3874.0   

      Township_wellcompletion Range_wellcompletion Meridian_wellcompletion  \
9499                     T13S                 R17E                     MDM   
92348                    T18S                 R25E                     MDM   
4504                     T15S                 R20E                     MDM

In [ ]:
combined_well_precip_reser_df.columns

Index(['LATITUDE_wellcompletion', 'LONGITUDE_wellcompletion', 'TOWNSHIP',
       'RANGE', 'SECTION', 'WELLLOCATION', 'CITY', 'COUNTY',
       'BOTTOMOFPERFORATEDINTERVAL', 'TOPOFPERFORATEDINTERVAL',
       'GROUNDSURFACEELEVATION', 'STATICWATERLEVEL', 'RECORDTYPE', 'USE',
       'WCRNUMBER', 'TOTALDRILLDEPTH', 'TOTALCOMPLETEDDEPTH', 'DATEWORKENDED',
       'CASINGDIAMETER', 'TOTALCOMPLETEDDEPTH_CORRECTED',
       'DATEWORKENDED_CORRECTED', 'year', 'MONTHWORKENDED',
       'geometry_wellcompletion', 'index_right_wellcompletion',
       'OBJECTID_wellcompletion', 'Township_wellcompletion',
       'Range_wellcompletion', 'Meridian_wellcompletion',
       'Source_wellcompletion', 'Section_wellcompletion',
       'MTRS_wellcompletion', 'TownshipRange', 'drought_year', 'station_id',
       'STATION NAME', 'OCT', 'NOV', 'DEC', 'JAN', 'FEB', 'MAR', 'APR', 'MAY',
       'JUN', 'JUL', 'AUG', 'SEP', 'average_year_precip',
       'LATITUDE_precipitation_station', 'LONGITUDE_precipitation_station',

In [ ]:
combined_well_precip_reser_df = combined_well_precip_reser_df[['WCRNUMBER',  'TownshipRange', 'COUNTY',
                                                               'BOTTOMOFPERFORATEDINTERVAL', 'TOPOFPERFORATEDINTERVAL',
                                                               'GROUNDSURFACEELEVATION', 'average_year_precip_corrected', 
                                                               'STATICWATERLEVEL', 'RECORDTYPE', 'USE',
                                                               'TOTALDRILLDEPTH', 'TOTALCOMPLETEDDEPTH', 'DATEWORKENDED',
                                                               'CASINGDIAMETER', 'TOTALCOMPLETEDDEPTH_CORRECTED',
                                                               'DATEWORKENDED_CORRECTED', 'year', 'MONTHWORKENDED',
                                                               'geometry_wellcompletion', 'MTRS_wellcompletion']].copy()

In [ ]:
combined_well_precip_reser_df[~combined_well_precip_reser_df.average_year_precip_corrected.isnull()]

WCRNUMBER TownshipRange   COUNTY  BOTTOMOFPERFORATEDINTERVAL  \
12     WCR2016-017657     T01S R04E  Alameda                       160.0   
20     WCR2015-013926     T02S R04E  Alameda                       680.0   
34     WCR2016-017810     T03S R11E  Alameda                       360.0   
35     WCR2018-010783     T02S R04E  Alameda                       500.0   
58     WCR2014-004482     T05N R09E   Amador                       266.0   
...               ...           ...      ...                         ...   
98075  WCR2015-011444     T04N R06E      NaN                       290.0   
98076  WCR2016-010754     T04N R07E      NaN                       205.0   
98077  WCR2015-012485     T04N R08E      NaN                       350.0   
98078  WCR2015-014442     T04N R05E      NaN                       165.0   
98079  WCR2014-014803     T04N R06E      NaN                       230.0   

       TOPOFPERFORATEDINTERVAL  GROUNDSURFACEELEVATION  \
12                        60.0                     NaN   
20                        80.0                     NaN   
34                       340.0                     NaN   
35                       140.0                     NaN   
58                       166.0                     NaN   
...                        ...                     ...   
98075                    210.0                     NaN   
98076                    145.0                     NaN   
98077                    250.0                     NaN   
98078                    105.0                     NaN   
98079                    170.0                     NaN   

       average_year_precip_corrected  STATICWATERLEVEL  \
12                          0.976895               7.0   
20                          0.676060               1.0   
34                          0.976895              40.0   
35                          0.560585               0.0   
58                          0.468700               NaN   
...                              ...               ...   
98075                       0.676060               NaN   
98076                       0.976895               NaN   
98077                       0.676060               NaN   
98078                       0.676060               NaN   
98079                       0.468700               NaN   

                                           RECORDTYPE          USE  \
12     WellCompletion/New/Production or Monitoring/NA     Domestic   
20     WellCompletion/New/Production or Monitoring/NA  Agriculture   
34     WellCompletion/New/Production or Monitoring/NA  Agriculture   
35     WellCompletion/New/Production or Monitoring/NA       Public   
58     WellCompletion/New/Production or Monitoring/NA  Agriculture   
...                                               ...          ...   
98075  WellCompletion/New/Production or Monitoring/NA     Domestic   
98076  WellCompletion/New/Production or Monitoring/NA     Domestic   
98077  WellCompletion/New/Production or Monitoring/NA     Domestic   
98078  WellCompletion/New/Production or Monitoring/NA     Domestic   
98079  WellCompletion/New/Production or Monitoring/NA     Domestic   

       TOTALDRILLDEPTH  TOTALCOMPLETEDDEPTH DATEWORKENDED  CASINGDIAMETER  \
12                 NaN                160.0    2016-06-13            10.0   
20                 NaN                710.0    2015-09-29            12.0   
34                 NaN                500.0    2016-01-08            30.0   
35               520.0                520.0    2018-11-22             NaN   
58                 NaN                325.0    2014-06-04            10.0   
...                ...                  ...           ...             ...   
98075              NaN                290.0    2015-05-19             6.0   
98076              NaN                205.0    2016-09-28             6.0   
98077              NaN                350.0    2015-03-04             6.0   
98078              NaN                165.0    2015-10-21             6.0   
98079            

In [ ]:
combined_well_precip_reser_df.columns

Index(['wcrnumber', 'townshiprange', 'county', 'bottomofperforatedinterval',
       'topofperforatedinterval', 'groundsurfaceelevation',
       'average_year_precip', 'staticwaterlevel', 'recordtype', 'use',
       'totaldrilldepth', 'totalcompleteddepth', 'dateworkended',
       'casingdiameter', 'totalcompleteddepth_corrected',
       'dateworkended_corrected', 'year', 'monthworkended',
       'geometry_wellcompletion', 'mtrs_wellcompletion'],
      dtype='object')

In [ ]:
precipitation_data_plss

<a style='text-decoration:none;line-height:16px;display:flex;color:#5B5B62;padding:10px;justify-content:end;' href='https://deepnote.com?utm_source=created-in-deepnote-cell&projectId=b042e2da-6536-449d-95b8-d85fa08825de' target="_blank">
 </img>
Created in <span style='font-weight:600;margin-left:4px;'>Deepnote</span></a>